## Make a program to choose randomly p fraction of the population to infect initially
* Randomly with choosen probability picks 0 and 1 
* We find list of all unique users and then we need to infect a percentage of population
* Again a problem here is that we need to start infecting users only after a particular time
* we need to make this set to be positive or negative

**I propose that there could be atleast two mechanism to start infection**
1. Randomly infect people by choosing them after a particular time
2. Randomly infect people by choosing a particular place at particular time (this is how COVID started)
3. If choosing step 2 then we can randmly infect people who were at that place at a particular time
4. Using alpha as infection rate

In [12]:
import pandas as pd

df = pd.read_csv("processedTMSC2014.tsv",sep='\t', engine="python")
df.drop(["Unnamed: 0"],axis=1, inplace=True)

/opt/anaconda3/lib/python3.7/site-packages/arcgis/features/_data/geodataset/utils.py:16: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  pd.datetime,


Import the ArcGIS API for Python. This adds a GeoAccessor and spatially enables your DataFrame objects. As you will see in this notebook, you can then easily plot your data both as charts and as maps.

In [14]:
import matplotlib.pyplot as plt
%matplotlib inline

from arcgis.gis import GIS
from arcgis.features import GeoAccessor, GeoSeriesAccessor

# EXTRA IDEAS
## We can use venue catorgories to define the probabilty of infection
* If it is a closed space we can have more probability 
* If it is public space which is frequented by many we can give more probability
* Also we can give probability of contamination by looking at how many people were there at the place at given time

In [2]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  
0                   0  1333476009  
1                   0  1333476025  
2                   0  1333476144  
3                   0  1333476161  
4                   0  1333476180  
...               ...         ...  
227423              0  1360981751  
227424              0  1360981895  
227425              0  1360981996  
227426              0  1360982071  
227427              0  1360982136  

[227428 rows x 13 columns]

# We set the randomly chosen population to be infected

In [3]:
import numpy as np

alpha = 0.1

#choosing unique users from list of all user IDs
unique_users =  pd.unique(df["User ID (anonymized)"])#.

print(f"Number of unique users are: {len(unique_users)}")

# this is when we are infecting people after a particular time
gen_positive = np.random.choice((1,0),size = len(unique_users), p=[alpha, 1-alpha])

#Choosing the time at which infection begins
infect_time = df.iloc[2000]["Time"]

infections = np.sum(gen_positive)
print(f"Number of infected users: {infections}")

Number of unique users are: 1083
Number of infected users: 97


In [4]:
#Query logic to select only those users whose user id and time matches or  those who are positive already
for i in range(len(unique_users)):
    #print(i)
    if gen_positive[i] == 1:
        #Below query gives sets status to 1 if infected userId and time condition matches
        df["Status"]= np.where( ( (df["User ID (anonymized)"] == unique_users[i]) & (df["Time"] >= infect_time) ) | (df["Status"] == 1),1,0)

# Setting infection time for all
df["InfectionTime"] = np.where(df["Status"]==1,infect_time,0)

count_infected = len(df[df["Status"]==1])
print(f"number of infect rows: {count_infected}")

number of infect rows: 19833


In [5]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  
0                   0  1333476009  
1                   0  1333476025  
2                   0  1333476144  
3                   0  1333476161  
4                   0  1333476180  
...               ...         ...  
227423              0  1360981751  
227424              0  1360981895  
227425              0  1360981996  
227426              0  1360982071  
227427              0  1360982136  

[227428 rows x 13 columns]

# We need to do following
* We need to find every person that has been infected
* for every person that has been infected we need to find the other person who was at same place and time range
* infect these people with certain probability


    print(f"Meeting population for \n{infector}")
    print(meeting_population, i)
    for j in range(0,len(meeting_population)):
        person = df.iloc[meeting_population[j]]
        if(person["Status"]==0):
            print("Non infected person met.................")
            if( person["Time"] >= infector["Time"] and person["Time"]<= infector["Time"]+3600):
                print("In range.............................")
                #Find all the entries of this person after this time and set details
                person_rows = list(np.where((df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0])
                print("Places where this person has rows")
                print(person_rows)
                for k in range(len(person_rows)):
                    df.iloc[meeting_population[j]]["Status"] = 1
                    df.iloc[meeting_population[j]]["InfectorId"] = infector["User ID (anonymized)"]
                    df.iloc[meeting_population[j]]["InfectionTime"] = person["Time"]
            else:
                print("Saved! Was not in time range of 1 hours for infection")
        else:
            # It might so happen that 1st infector was not processed to infect first
            if( person["Time"] >= infector["Time"] and person["Time"]<= infector["Time"]+3600):
                print("In range.............................")
          
                if(person["InfectionTime"] >= person["Time"]):
                    print("Infected already........")
                else:
                    #Find all the entries of this person after this time and set details
                    print("Updating new infector.....................")
                    person_rows = list(np.where((df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0])
                    print("Places where this person has rows")
                    print(person_rows)
                    for k in range(len(person_rows)):
                        df.iloc[meeting_population[j]]["Status"] = 1
                        df.iloc[meeting_population[j]]["InfectorId"] = infector["User ID (anonymized)"]
                        df.iloc[meeting_population[j]]["InfectionTime"] = person["Time"]
            else:
                print("Saved! Was not in time range of 1 hours for infection")
    

In [6]:
# Find all the infected rows
infected_users_dataframe = df[df["Status"]==1]
print("List of infected users")
infected_users_dataframe

List of infected users


User ID (anonymized)     Venue ID (Foursquare)  \
2014                      32  45940e37f964a52055401fe3   
2021                     619  4c1163e2416620a14304d9e4   
2047                     335  4b61a925f964a520231c2ae3   
2048                     335  4df2f04dd4c01ff6b2eaca87   
2050                     335  4b93d226f964a520625334e3   
...                      ...                       ...   
227371                   729  4cfefa18c00a5941688a8f87   
227380                   314  50c3cbbce4b085c8e4119be8   
227381                   875  49f47a7af964a5200a6b1fe3   
227385                   401  4ff6166ad63e98a6803f743f   
227396                    36  4b302460f964a520cdf624e3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
2014         4bf58dd8d48988d1f5941735               Food & Drink Shop   
2021         4bf58dd8d48988d1ff941735              Miscellaneous Shop   
2047         4bf58dd8d48988d12a951735                   Train Station   
2048         4bf58dd8d48988d162941735            Other Great Outdoors   
2050         4bf58dd8d48988d129951735                   Train Station   
...                               ...                             ...   
227371       4bf58dd8d48988d130941735                        Building   
227380       4d954b0ea243a5684a65b473               Convenience Store   
227381       4bf58dd8d48988d120941735                             Bar   
227385       4bf58dd8d48988d1d1941735           Ramen /  Noodle House   
227396       4bf58dd8d48988d11d941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
2014    40.742870 -73.982438                      -240   
2021    40.746164 -73.987046                      -240   
2047    40.662638 -73.908870                      -240   
2048    40.664211 -73.914750                      -240   
2050    40.664796 -73.922954                      -240   
...           ...        ...                       ...   
227371  40.769399 -73.985600                      -300   
227380  40.749021 -74.136357                      -300   
227381  40.749443 -73.984865                      -300   
227385  40.682688 -73.993134                      -300   
227396  40.739110 -74.030474                      -300   

                              UTC time  Status  Iteration  InfectorId  \
2014    Wed Apr 04 17:25:36 +0000 2012       1          0           0   
2021    Wed Apr 04 17:28:19 +0000 2012       1          0           0   
2047    Wed Apr 04 17:43:33 +0000 2012       1          0           0   
2048    Wed Apr 04 17:43:50 +0000 2012       1          0           0   
2050    Wed Apr 04 17:45:16 +0000 2012       1          0           0   
...                                ...     ...        ...         ...   
227371  Thu Feb 14 12:29:55 +0000 2013       1          0           0   
227380  Sat Feb 16 01:42:05 +0000 2013       1          0           0   
227381  Sat Feb 16 01:43:57 +0000 2013       1          0           0   
227385  Sat Feb 16 01:48:28 +0000 2013       1          0           0   
227396  Sat Feb 16 02:01:16 +0000 2013       1          0           0   

        InfectionTime        Time  
2014       1333559854  1333560336  
2021       1333559854  1333560499  
2047       1333559854  1333561413  
2048       1333559854  1333561430  
2050       1333559854  1333561516  
...               ...         ...  
227371     1333559854  1360844995  
227380     1333559854  1360978925  
227381     1333559854  1360979037  
227385     1333559854  1360979308  
227396     1333559854  1360980076  

[19833 rows x 13 columns]

In [7]:
# Find all the infected users
infected_users_dataframe = df[df["Status"]==1]
infected_users = pd.unique(infected_users_dataframe["User ID (anonymized)"])
print("Infected Users are: ")
print(infected_users)
#count number of infections
infections = len(infected_users)
print(f"Total infections are: {infections}")
# Infection list stores list of infected people per round of simulation
infection_list = []
infection_list.append(infected_users)
# We need to find all the users who where at the same place as the infected user and in time range of 1 hrs
# 1hr = 3600 seconds
# ITERATING OVER ALL ROWS AND CHECKING TIME
iteration_count = 0
while(infections!=0):
    # we will maintain this variable to fetch inly new infections
    print("#############################################################################")
    print("#############################################################################")
    print("#############################################################################")
    infected_rows = len(infected_users_dataframe)
    for i in range(infected_rows):
        print(f"Calculating for infected person: {i} of {infected_rows}")
        infector = infected_users_dataframe.iloc[i]
        
        ##print("Infector is:")
        ##print("###################################################################")
        ##print(infector)
        ##print("###################################################################")
        
        # Finding all those prople infector meets after start of infection time
        # meeting_population =  list(np.where( (df["Latitude"] == infector["Latitude"]) & (df["Longitude"] == infector["Longitude"])  & (df["Time"] >= infect_time))[0])
        
        # Finding all people that infector meets at infectors time range
        # Meeting Population is the list of indices of the people, not the User Id (anonymized)
        # We are keeping 3 hours time window -1 +2
        
        meeting_population =  list(np.where( (df["Latitude"] == infector["Latitude"]) & (df["Longitude"] == infector["Longitude"]) & ( (df["Time"] >= (infector["Time"]-3600)) & (df["Time"] <= (infector["Time"]+7200)) ))[0])
        
        print("List of people this infector meets: "+str({len(meeting_population)})) 
        ##print(meeting_population)
        ##print(meeting_population)
        
        for index in meeting_population:
            person = df.iloc[index]
            if(person["Status"]==0):
                
                print(f"Non infected person met.................{index}")
                ##print("In range.............................")
                #Find all the entries of this person after this time and set details
                
                person_rows = np.where( (df["User ID (anonymized)"]==person["User ID (anonymized)"]) & (df["Time"]>=person["Time"]))[0]
                
                ##print("Places where this person has rows")
                ##print(f"Rows of person is : {len(person_rows)}")
                
                # TO MAKE MORE EFFIECIENT
                # https://stackoverflow.com/questions/49447233/python-maintain-multiple-columns-with-np-where
                for k in range(len(person_rows)):
                    df.at[index, "Status"] = 1
                    #print("Status Set")
                    df.at[index, "InfectorId"] = infector["User ID (anonymized)"]
                    #print("Infector Id Set")
                    df.at[index, "InfectionTime"] = person["Time"]
                    #print("Infection Time Set")
                    df.at[index, "Iteration"] = iteration_count+1
                    df.at[index, "InfectionLongitude"] = infector["Longitude"]
                    df.at[index, "InfectionLatitude"] = infector["Latitude"]
            else:
                # AS data is sorted with time we assume that we don't need tp bother who infects first
                print(f"Met with an already infected person.................{index}")
                
    # Find all the infected users
    # HERE WE MUST ALSO SET CONDITIONS BASED ON ITERATION, FETCH ONLY THAT WERE INFECTED IN THIS ITERATION
    iteration_count += 1
    print("Finding new Infections............................")
    infected_users_dataframe = df[(df["Status"]==1) & (df["Iteration"]==iteration_count)]
    infected_users = pd.unique(infected_users_dataframe["User ID (anonymized)"])
    infection_list.append(infected_users)
    ##print("Infected Users are: ")
    ##print(infected_users)
    #count number of infections
    print("Infected Users are: ")
    print(infected_users)
    infections = len(infected_users)
    print(f"Total new infections are: {infections}") 
    print("#############################################################################")
    print("#############################################################################")
    print("#############################################################################")

Infected Users are: 
[  32  619  335  238  827  314  315  196  563  881  770   54  495  908
 1014  438  210  877  769  338  941  922  693  258  673  433  207  990
  895  465  186  327 1064  907   83  162  401  139  833  342  308  853
   87  903  788  241  750  880  114  625  360  245  677  367  568  469
  871  964  679 1026  716  892  230  108 1036 1011  392  695  703  803
 1034  175  396  190  421  887  938  172  843  234  900  795  585  416
   28  773  460  729  502  875  209  146   36  547  899  336 1081]
Total infections are: 97
#############################################################################
#############################################################################
#############################################################################
Calculating for infected person: 0 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2014
Calculating for infected person: 1 of 19833
List of people this infector meets: {1}
Me

List of people this infector meets: {1}
Met with an already infected person.................2674
Calculating for infected person: 62 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2716
Calculating for infected person: 63 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2766
Calculating for infected person: 64 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2778
Calculating for infected person: 65 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2784
Calculating for infected person: 66 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2798
Calculating for infected person: 67 of 19833
List of people this infector meets: {1}
Met with an already infected person.................2801
Calculating for infected person: 68 of 19833
List o

List of people this infector meets: {1}
Met with an already infected person.................3586
Calculating for infected person: 125 of 19833
List of people this infector meets: {1}
Met with an already infected person.................3588
Calculating for infected person: 126 of 19833
List of people this infector meets: {1}
Met with an already infected person.................3607
Calculating for infected person: 127 of 19833
List of people this infector meets: {1}
Met with an already infected person.................3663
Calculating for infected person: 128 of 19833
List of people this infector meets: {1}
Met with an already infected person.................3711
Calculating for infected person: 129 of 19833
List of people this infector meets: {1}
Met with an already infected person.................3717
Calculating for infected person: 130 of 19833
List of people this infector meets: {1}
Met with an already infected person.................3731
Calculating for infected person: 131 of 19833

List of people this infector meets: {2}
Met with an already infected person.................4612
Met with an already infected person.................4678
Calculating for infected person: 187 of 19833
List of people this infector meets: {1}
Met with an already infected person.................4712
Calculating for infected person: 188 of 19833
List of people this infector meets: {1}
Met with an already infected person.................4717
Calculating for infected person: 189 of 19833
List of people this infector meets: {1}
Met with an already infected person.................4719
Calculating for infected person: 190 of 19833
List of people this infector meets: {1}
Met with an already infected person.................4728
Calculating for infected person: 191 of 19833
List of people this infector meets: {1}
Met with an already infected person.................4753
Calculating for infected person: 192 of 19833
List of people this infector meets: {1}
Met with an already infected person..........

Calculating for infected person: 243 of 19833
List of people this infector meets: {1}
Met with an already infected person.................5232
Calculating for infected person: 244 of 19833
List of people this infector meets: {1}
Met with an already infected person.................5306
Calculating for infected person: 245 of 19833
List of people this infector meets: {1}
Met with an already infected person.................5310
Calculating for infected person: 246 of 19833
List of people this infector meets: {1}
Met with an already infected person.................5319
Calculating for infected person: 247 of 19833
List of people this infector meets: {24}
Non infected person met.................5248
Non infected person met.................5250
Non infected person met.................5267
Non infected person met.................5286
Non infected person met.................5314
Non infected person met.................5315
Non infected person met.................5323
Met with an already infect

...

List of people this infector meets: {2}
Met with an already infected person.................116735
Met with an already infected person.................116790
Calculating for infected person: 48 of 104
List of people this infector meets: {23}
Met with an already infected person.................121253
Met with an already infected person.................121257
Met with an already infected person.................121278
Met with an already infected person.................121291
Met with an already infected person.................121292
Met with an already infected person.................121297
Met with an already infected person.................121298
Met with an already infected person.................121302
Met with an already infected person.................121314
Met with an already infected person.................121328
Met with an already infected person.................121329
Met with an already infected person.................121330
Met with an already infected person...............

Met with an already infected person.................121504
Met with an already infected person.................121511
Calculating for infected person: 56 of 104
List of people this infector meets: {12}
Met with an already infected person.................121420
Met with an already infected person.................121465
Met with an already infected person.................121466
Met with an already infected person.................121467
Met with an already infected person.................121471
Met with an already infected person.................121474
Met with an already infected person.................121483
Met with an already infected person.................121493
Met with an already infected person.................121503
Met with an already infected person.................121504
Met with an already infected person.................121511
Met with an already infected person.................121574
Calculating for infected person: 57 of 104
List of people this infector meets: {12}
Met wi

Met with an already infected person.................200572
Met with an already infected person.................200597
Met with an already infected person.................200605
Met with an already infected person.................200611
Met with an already infected person.................200623
Met with an already infected person.................200650
Met with an already infected person.................200666
Met with an already infected person.................200683
Calculating for infected person: 92 of 104
List of people this infector meets: {8}
Met with an already infected person.................200572
Met with an already infected person.................200597
Met with an already infected person.................200605
Met with an already infected person.................200611
Met with an already infected person.................200623
Met with an already infected person.................200650
Met with an already infected person.................200666
Met with an already infected per

Calculating for infected person: 2 of 26
List of people this infector meets: {2}
Met with an already infected person.................49492
Non infected person met.................49663
Calculating for infected person: 3 of 26
List of people this infector meets: {7}
Met with an already infected person.................50323
Met with an already infected person.................50373
Met with an already infected person.................50414
Met with an already infected person.................50443
Met with an already infected person.................50456
Met with an already infected person.................50458
Met with an already infected person.................50482
Calculating for infected person: 4 of 26
List of people this infector meets: {5}
Met with an already infected person.................65625
Met with an already infected person.................65629
Met with an already infected person.................65737
Met with an already infected person.................65760
Non infected pe

Calculating for infected person: 1 of 9
List of people this infector meets: {4}
Met with an already infected person.................12332
Met with an already infected person.................12427
Met with an already infected person.................12463
Met with an already infected person.................12702
Calculating for infected person: 2 of 9
List of people this infector meets: {2}
Met with an already infected person.................49663
Non infected person met.................49872
Calculating for infected person: 3 of 9
List of people this infector meets: {2}
Met with an already infected person.................65859
Met with an already infected person.................65928
Calculating for infected person: 4 of 9
List of people this infector meets: {4}
Met with an already infected person.................65859
Met with an already infected person.................65928
Non infected person met.................66045
Non infected person met.................66054
Calculating for infe

In [8]:
#Check number of infection rounds
len(infection_list)

9

In [9]:
# Check number of infections per round
y = [len(x) for x in infection_list]
y


[97, 584, 185, 84, 25, 9, 6, 4, 0]

In [10]:
# Total infected individuals 
sum(y)

994

In [11]:
# Write infected dataframe to the file
df.to_csv("NYCInfectedTMSC2014.tsv", sep="\t")

# Visualization

In [17]:
df = pd.read_csv("NYCInfectedTMSC2014.tsv",sep='\t', engine="python")
df.drop(["Unnamed: 0"],axis=1, inplace=True)

gis = GIS()

In [18]:
df

User ID (anonymized)     Venue ID (Foursquare)  \
0                        470  49bbd6c0f964a520f4531fe3   
1                        979  4a43c0aef964a520c6a61fe3   
2                         69  4c5cc7b485a1e21e00d35711   
3                        395  4bc7086715a7ef3bef9878da   
4                         87  4cf2c5321d18a143951b5cec   
...                      ...                       ...   
227423                   688  3fd66200f964a52000e71ee3   
227424                   560  4bca32ff0687ef3be789dbcc   
227425                   945  50a77716e4b0b5a9492f6f56   
227426                   671  4514efe0f964a520e7391fe3   
227427                   942  4a1e0ca0f964a520bf7b1fe3   

       Venue category ID (Foursquare) Venue category name (Fousquare)  \
0            4bf58dd8d48988d127951735             Arts & Crafts Store   
1            4bf58dd8d48988d1df941735                          Bridge   
2            4bf58dd8d48988d103941735                  Home (private)   
3            4bf58dd8d48988d104941735                  Medical Center   
4            4bf58dd8d48988d1cb941735                      Food Truck   
...                               ...                             ...   
227423       4bf58dd8d48988d1e7931735                     Music Venue   
227424       4bf58dd8d48988d16c941735                    Burger Joint   
227425       4bf58dd8d48988d103941735                  Home (private)   
227426       4bf58dd8d48988d11d941735                             Bar   
227427       4bf58dd8d48988d116941735                             Bar   

         Latitude  Longitude  Timezone offset(minutes)  \
0       40.719810 -74.002581                      -240   
1       40.606800 -74.044170                      -240   
2       40.716162 -73.883070                      -240   
3       40.745164 -73.982519                      -240   
4       40.740104 -73.989658                      -240   
...           ...        ...                       ...   
227423  40.733596 -74.003139                      -300   
227424  40.745719 -73.993720                      -300   
227425  40.854364 -73.883070                      -300   
227426  40.735981 -74.029309                      -300   
227427  40.726805 -73.957422                      -300   

                              UTC time  Status  Iteration  InfectorId  \
0       Tue Apr 03 18:00:09 +0000 2012       0          0           0   
1       Tue Apr 03 18:00:25 +0000 2012       0          0           0   
2       Tue Apr 03 18:02:24 +0000 2012       0          0           0   
3       Tue Apr 03 18:02:41 +0000 2012       0          0           0   
4       Tue Apr 03 18:03:00 +0000 2012       0          0           0   
...                                ...     ...        ...         ...   
227423  Sat Feb 16 02:29:11 +0000 2013       0          0           0   
227424  Sat Feb 16 02:31:35 +0000 2013       0          0           0   
227425  Sat Feb 16 02:33:16 +0000 2013       0          0           0   
227426  Sat Feb 16 02:34:31 +0000 2013       0          0           0   
227427  Sat Feb 16 02:35:36 +0000 2013       0          0           0   

        InfectionTime        Time  InfectionLongitude  InfectionLatitude  
0                   0  1333476009                 NaN                NaN  
1                   0  1333476025                 NaN                NaN  
2                   0  1333476144                 NaN                NaN  
3                   0  1333476161                 NaN                NaN  
4                   0  1333476180                 NaN                NaN  
...               ...         ...                 ...                ...  
227423              0  1360981751                 NaN                NaN  
227424              0  1360981895                 NaN                NaN  
227425              0  1360981996                 NaN                NaN  
227426              0  1360982071                 NaN                NaN  
227427              0  1360982136  

In [15]:
print(infection_list[0])

[  32  619  335  238  827  314  315  196  563  881  770   54  495  908
 1014  438  210  877  769  338  941  922  693  258  673  433  207  990
  895  465  186  327 1064  907   83  162  401  139  833  342  308  853
   87  903  788  241  750  880  114  625  360  245  677  367  568  469
  871  964  679 1026  716  892  230  108 1036 1011  392  695  703  803
 1034  175  396  190  421  887  938  172  843  234  900  795  585  416
   28  773  460  729  502  875  209  146   36  547  899  336 1081]


In [19]:
df.shape

(227428, 15)

In [20]:
df.columns

Index(['User ID (anonymized)', 'Venue ID (Foursquare)',
       'Venue category ID (Foursquare)', 'Venue category name (Fousquare)',
       'Latitude', 'Longitude', 'Timezone offset(minutes)', 'UTC time',
       'Status', 'Iteration', 'InfectorId', 'InfectionTime', 'Time',
       'InfectionLongitude', 'InfectionLatitude'],
      dtype='object')